<a href="https://colab.research.google.com/github/AnnCzar/Dot-Plot-Algorithm/blob/main/Anna_Czarnasiak_lista1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Lista nr 1
## Anna Czarnasiak, 268319

In [1]:
import numpy as np
import plotly.express as px

import requests as r
import re
import plotly.express as px




# Wczytanie sekwencji
## Pseudokod
```python
Funkcja open_seq(sciezka_lub_id):


    Jeśli ".fasta" znajduje się w sciezka_lub_id:
        To  spróbuj otwórzyć plik
        Jeśli się nie uda to zwróć błąd FileNotFoundError:

    W przeciwnym razie:
        Ściągnij dane z strony uniprot
        aktualny_url = url + sciezka_lub_id + ".fasta"
        odpowiedz = WYSYŁAJ_ZAPYTANIE_HTTP(aktualny_url)
        odczyt = odpowiedz.tekst

    wzorzec_alf = wzorzec_regex_do_sprawdzenia_dozwolonych_znakow_sekwencji

    Jeśli ">" znajduje się w otworzonym pliku:
        T0 wyciągnij sekwencje i konweruj jej zawartoś na wielkie litery

        Jeżeli sekwencja zawiera nieakceptowalne znaki:
            wywołaj ValueError
        w przeciwnym razie:
            zwróć sekwencje
    w przeciwnym razie:
        wywołaj ValueError


In [2]:
def open_seq(path_or_id):

    """
    Opening a file based on the provided path or fetching data from the Uniprot website based on the given ID and extracting the sequence.

    Args:
    path_or_id (str): Path to the file or protein ID

    Returns:
    str: Extracted sequence

    Raises:
    FileNotFoundError: If the file is not found
    ValueError: If the extracted sequence does not have a valid format
    """

    url="http://www.uniprot.org/uniprot/"
        # url = f"https://www.uniprot.org/uniprot/{path_or_id}.fasta"
    seq = " "
    read = ''

    if ".fasta" in path_or_id:
        try:
            f = open(path_or_id, "r")
            read = f.read()

        except FileNotFoundError:
                print("Not found your file")
    else:
            currentUrl = url + path_or_id + ".fasta"
            response = r.post(currentUrl)
            read= response.text

    seq_alf = r'[ACDEFGHIKLMNPQRSTUVWY]+'


    if ">" in read:
        sequence = ''.join(read.split('\n')[1:])
        sequence.upper()

        if bool(re.fullmatch( seq_alf , sequence)) == False:
            raise ValueError("Sequence contains unacceptable characters")
        else:
            return sequence
    else:
        raise ValueError("Header do not start with >")


# Wygenerowanie macierzy kropkowej
## Pseudokod

```python
FUNKCJA matrix_dot(seq1, seq2):
    JEŚLI seq1 lub seq2 są równe None TO
        WYWOŁAJ ValueError

    USTAW matrix_d jako macierz zer o wymiarach( długość seq 1 i długość seq2)
    
    DLA KAŻDEGO i W ZAKRESIE (długość(seq1)):
        DLA KAŻDEGO j W ZAKRESIE (długość(seq2)):
            JEŚLI seq1[i] == seq2[j] TO
                 ustaw matrix_d[i, j] na 1

    ZWRÓĆ matrix_d


In [4]:

def matrix_dot(seq1, seq2):
    """
    Creating a zero-one matrix based on the alignment of two sequences.

    Args:
        seq1 (str): First sequence - aligned vertically
        seq2 (str): Second sequence - aligned horizontally

    Returns:
        array: Matrix of zeros and ones

    Raises:
        ValueError: if the sequences do not contain characters
    """

    if seq1 == None or seq2 == None:
        raise ValueError("Input sequences cannot be empty")

    matrix_d = np.zeros((len(seq1), len(seq2)))
    for i in range(len(seq1)):
        for j in  range(len(seq2)):
            if seq1[i] == seq2[j]:
                matrix_d[i, j] = 1

    return matrix_d




# Filtrowanie macierzy kropkowej dla zadanych rozmiary okna i progu filtra
## Pseudokod


In [5]:



def diagonals(matrix):
    """
    Extracts diagonals from a given matrix.

    Parameters:
        matrix (numpy.ndarray): Input matrix.

    Returns:
        list: List of diagonal arrays.
    """
    rows, columns = matrix.shape
    diagonals = []
    for i in range(1,rows, 1):
        diagonal = np.diag(matrix, k = rows - i)
        diagonals.append(diagonal)

    for j in range(0,-columns,-1):
        diagonal = np.diag(matrix, k = j)
        diagonals.append(diagonal)

    return diagonals


def wind (diagonals, threshold, window):
    """
    Filters diagonals based on a given threshold and window size.

    Parameters:
        diagonals (list): List of diagonal arrays.
        threshold (int): Threshold value for filtering.
        window (int): Size of the filtering window.

    Returns:
        list: List of filtered diagonal arrays.
    """

    newDiagonals = []
    for j in range(len(diagonals)):
        diagonal = diagonals[j].copy()
        for i in range(len(diagonal)):
            win_diag = diagonal[i:i+window]
            if np.sum(win_diag) < threshold:
                diagonal[i] = 0

        newDiagonals.append(diagonal)
    return newDiagonals


def filtr_matrix (matrix1, treshold, window):
    """
    Applies diagonal filtering to a given matrix.

    Parameters:
        matrix1 (numpy.ndarray): Matrix to be filtered.
        threshold (int): Threshold value for filtering.
        window (int): Size of the filtering window.

    Returns:
        numpy.ndarray: Filtered matrix.
    """
    if (treshold< 0 or window <= 0):
        raise ValueError ("Treshold/Window cannot be negative")


    diagonals1 = diagonals(matrix1)
    final_diagonals = wind(diagonals1, treshold, window)
    max_row, max_col = matrix1.shape

    final_matrix = np.zeros((max_row,max_col), dtype=int)


    for col_index in range(max_col):
        diagonal_index = col_index
        np.fill_diagonal(final_matrix[:,max_col-col_index-1:], final_diagonals[diagonal_index])

    for row_index in range(1, max_row):
        diagonal_index = max_col + row_index - 1
        np.fill_diagonal(final_matrix[row_index:], final_diagonals[diagonal_index])

    return final_matrix








# Analiza złożoności obliczeniowej
* Funkcja Open_seq - $O(n)$
* Funkcja Matrix_dot - $O(n)$
* Funkjca Diagonals - $O(n^2)$
* Funkcja Function - $O(n^2)$
* Funkcja Filtr_matrix - $O(n^2)$


Podsumowując, całkowita złożoność obiczeniowa wynosi:
$O(n+ n +n^2+n^2+n^2)$, co daje $O(3n^2+2n)$ = $O(n^2)$.

# Porównanie przykładowych par sekwencji powiązanych
## Przykład wywołania kodu


In [6]:

# seq1 = open_seq('TAU_HUMAN.fasta')
# seq2 = open_seq('TAU_MOUSE.fasta')

seq1 = open_seq('P38398')
seq2 = open_seq('Q95153')


matriz_seq = matrix_dot(seq2, seq1)
final_dotplot1 = filtr_matrix(matriz_seq, 8 , 19)


In [8]:


def save_fig1(matrix, threshold, window):

    fig = px.imshow(matrix, color_continuous_scale=[[0, 'white'], [1, 'blue']],
                    color_continuous_midpoint=0.5, origin='lower')
    fig.update_layout(width=1100, height=900, title = f'Dotplot dla sekwencji TAU człowieka i myszy, threshold = {threshold}, window = {window}',
                      title_x = 0.5,
                      coloraxis_colorbar=dict(outlinewidth=0, ticks=""),
                      coloraxis_showscale=False,
                      xaxis_title="TAU człowieka", yaxis_title="TAU myszy",
                      xaxis_showline=True, yaxis_showline=True,
                      xaxis_linecolor='black', yaxis_linecolor='black')
    fig.update_xaxes(showticklabels=True).update_yaxes(showticklabels=True)
    fig.show()


    # filename = f"dp_seq_th{threshold}_w{window}.png"
    # fig.write_image(filename)


save_fig1(final_dotplot1, 8, 19)



# Interpretacja macierzy kropkowej dla przykładowych par TAU człowieka i TAU myszy
Na podstawie powyższego dot plota można zauważyć, że sekwencje są do siebie podobne, jednakże nie są one identyczne. Objawia się to tym, że punkty układają się na linii prostej. Można stwierdzić, że w sekwncji doszło do substytucji, co charakteryzuje się przerwami w powstałej linii.

Ponadto, analiza macierzy kropkowej może wskazywać na obecność powtórzeń wewnętrznych, czyli sekwencji, które pojawiają się więcej niż raz w określonym miejscu. Można to zaobserwować w fragmentach, gdzie punkty układają się w pewien uporządkowany sposób, niekoniecznie na głównej prostej, ale powyżej lub poniżej niej.

# Porównanie przykładowych par sekwencji niepowiązanych
## Przykład wywołania kodu


In [10]:
seq1 = open_seq('P10636')
seq2 = open_seq('B6VQ60')

# seq1 = open_seq('TAU_HUMAN.fasta')
# seq2 = open_seq('BRCA1_CAEEL.fasta')



matriz_seq1 = matrix_dot(seq1, seq2)
final_dotplot2 = filtr_matrix(matriz_seq1, 2 , 10)



def save_fig2(matrix, threshold, window):

    fig = px.imshow(matrix, color_continuous_scale=[[0, 'white'], [1, 'blue']],
                    color_continuous_midpoint=0.5, origin='lower')
    fig.update_layout( title = f'Dotplot dla sekwencji TAU człowieka i BRCA1_CAEEL, threshold = {threshold}, window = {window}',
                      title_x = 0.5,
                      coloraxis_colorbar=dict(outlinewidth=0, ticks=""),
                      coloraxis_showscale=False,
                      xaxis_title="BRCA1_CAEEL", yaxis_title="TAU człowieka",
                      xaxis_showline=True, yaxis_showline=True,
                      xaxis_linecolor='black', yaxis_linecolor='black')
    fig.update_xaxes(showticklabels=True).update_yaxes(showticklabels=True)
    fig.show()


    # filename = f"dp_seq_th{threshold}_w{window}.png"
    # fig.write_image(filename)


save_fig2(final_dotplot2, 2, 10)

# Interpretacja macierzy kropkowej dla przykładowych par TAU człowieka i BRCA1_CAEEL


Na podstawie analizy macierzy kropkowej można stwierdzić, że analizowane sekwencje, tj. TAU u człowieka i BRCA1_CAEEL, nie wykazują podobieństwa między sobą. W przeciwieństwie do wcześniejszego przykładu, wspólne aminokwasy są rozproszone po całej przestrzeni wykresu, nie tworząc linii prostej. Brak podobieństwa między tymi sekwencjami wynika z faktu, że nie są one ze sobą ewolucyjnie powiązane.